# Retail Data Wrangling and Analytics

In [0]:
file_location = "/FileStore/tables/retail.csv"

retail_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(file_location)

retail_df.printSchema()


root
 |-- invoice_no: string (nullable = true)
 |-- stock_code: string (nullable = true)
 |-- description: string (nullable = true)
 |-- quantity: integer (nullable = true)
 |-- invoice_date: timestamp (nullable = true)
 |-- unit_price: double (nullable = true)
 |-- customer_id: integer (nullable = true)
 |-- country: string (nullable = true)



In [0]:
retail_df.show()

+----------+----------+--------------------+--------+-------------------+----------+-----------+--------------+
|invoice_no|stock_code|         description|quantity|       invoice_date|unit_price|customer_id|       country|
+----------+----------+--------------------+--------+-------------------+----------+-----------+--------------+
|    489434|     85048|15CM CHRISTMAS GL...|      12|2009-12-01 07:45:00|      6.95|      13085|United Kingdom|
|    489434|    79323P|  PINK CHERRY LIGHTS|      12|2009-12-01 07:45:00|      6.75|      13085|United Kingdom|
|    489434|    79323W| WHITE CHERRY LIGHTS|      12|2009-12-01 07:45:00|      6.75|      13085|United Kingdom|
|    489434|     22041|"RECORD FRAME 7""...|      48|2009-12-01 07:45:00|       2.1|      13085|United Kingdom|
|    489434|     21232|STRAWBERRY CERAMI...|      24|2009-12-01 07:45:00|      1.25|      13085|United Kingdom|
|    489434|     22064|PINK DOUGHNUT TRI...|      24|2009-12-01 07:45:00|      1.65|      13085|United K

# Total Invoice Amount Distribution

In [0]:
from pyspark.sql.functions import col, round, sum as _sum

# Calculate amount
amount_df = retail_df.withColumn("amount", col("quantity") * col("unit_price"))

# Group by invoice_no and round + alias 
amount_df = amount_df.groupBy("invoice_no").agg(
    round(_sum("amount"), 2).alias("total_amount")
).filter(col("total_amount") > 0)

amount_df = amount_df.orderBy(col("invoice_no").asc())

quantile_85 = amount_df.approxQuantile("total_amount", [0.85], 0.01)[0]

amount_df_85 = amount_df.filter(col("total_amount") < quantile_85)


In [0]:
from pyspark.sql.functions import min, max, median, mode, mean

def show_distribution(amounts):
    min_value = amounts.select(min("total_amount").alias("min_amount")).collect()[0]["min_amount"]
    max_value = amounts.select(max("total_amount").alias("max_amount")).collect()[0]["max_amount"]
    median_value = amounts.select(median("total_amount").alias("median")).collect()[0]["median"]
    mode_value = amounts.select(mode("total_amount").alias("mode")).collect()[0]["mode"]
    mean_value = amounts.select(mean("total_amount").alias("mean")).collect()[0]["mean"] 

    print('Minimum:{:.2f}\nMean:{:.2f}\nMedian:{:.2f}\nMode:{:.2f}\nMaximum:{:.2f}\n'.format(min_value,mean_value,median_value,mode_value,max_value))

    display(amounts)

total_amount = amount_df.select("total_amount")

show_distribution(total_amount)

Minimum:0.19
Mean:523.30
Median:304.31
Mode:15.00
Maximum:168469.60



total_amount 505.3 145.8 630.33 310.75 2286.24 426.3 50.4 344.34 382.37 285.06 141.0 308.44 996.1 130.0 570.24 196.1 485.79 589.33 148.3 1197.8 251.1 255.5 823.02 282.46 696.73 733.63 700.31 1160.0 1.4 929.92 229.46 145.0 304.53 192.75 367.41 633.33 2887.14 537.96 387.6 281.82 124.95 584.5 641.45 390.86 482.3 278.61 379.65 603.94 291.58 128.6 859.1 246.86 229.6 322.9 218.55 307.8 282.28 156.71 507.49 580.02 551.33 367.28 319.66 219.82 261.0 124.83 293.95 21.95 105.85 263.42 362.78 423.87 322.33 17.0 5097.82 822.37 2454.68 420.29 337.2 440.07 311.55 383.87 2.1 446.98 9.75 553.78 2.95 629.78 12.75 408.85 499.36 409.27 198.0 6.35 19.5 17.4 352.85 535.9 7.5 31.2 329.91 622.1 12.85 896.54 261.74 173.1 294.14 60.78 222.12 1237.3 55.2 828.09 23.48 73.75 374.43 252.3 263.09 538.46 378.12 397.2 114.6 740.3 772.65 61.1 261.3 4939.22 1210.8 192.0 189.3 795.98 45.0 89.59 125.73 1317.97 266.6 221.53 299.7 306.95 401.7 3108.64 17.0 2052.12 216.0 750.0 900.0 180.45 168.0 538.77 754.2 223.1 285.59 130.18 159.98 230.46 162.04 40.8 333.67 216.86 319.54 119.16 80.4 131.12 221.19 923.79 260.36 58.2 935.01 311.5 200.63 311.69 408.07 128.48 174.52 251.17 454.35 180.13 109.84 112.5 493.25 634.29 597.69 824.18 132.55 284.55 340.2 294.3 618.43 371.27 87.3 176.88 174.1 85.95 445.7 472.47 637.04 1008.0 316.22 150.68 214.8 714.0 514.97 89.7 157.91 4463.74 5741.96 46.07 734.7 66.82 206.85 234.87 1003.83 118.95 675.0 39.98 162.1 735.7 632.9 10.2 176.6 530.76 39.85 368.1 143.11 163.47 380.28 578.28 3.61 597.4 4734.24 976.8 181.08 39.8 300.1 520.2 371.82 337.93 260.44 287.37 119.1 203.78 478.7 120.0 202.06 107.33 642.2 144.0 1146.1 69.6 993.0 54.6 336.0 82.6 181.65 430.9 320.4 321.65 154.2 143.06 169.5 114.55 317.55 912.56 556.75 344.4 503.93 285.09 1008.0 221.69 763.35 500.55 744.21 393.65 4380.0 308.6 37.8 10.2 45.6 189.15 215.0 58.2 69.82 180.39 228.3 263.85 1146.71 102.0 13.5 831.0 119.54 277.5 61.12 360.52 47.85 14475.0 314.22 4000.0 165.3 210.39 355.59 1260.0 372.2 952.61 284.3 161.4 236.25 294.85 194.65 258.1 6500.63 381.0 115.51 584.35 160.35 311.7 723.09 337.9 2506.14 170.06 799.2 898.18 17.0 466.2 45.55 636.0 510.87 1794.7 851.76 186.36 279.42 1225.98 869.93 338.5 314.37 110.7 239.68 415.0 30.15 321.21 313.19 39.2 257.62 342.6 122.4 317.04 108.75 112.03 319.87 297.05 569.18 241.8 197.3 151.65 387.87 174.85 160.69 339.78 210.55 407.22 308.75 1261.0 1610.52 337.1 989.18 510.64 6529.11 160.39 682.65 290.48 455.36 138.0 508.26 19.5 244.8 825.94 280.2 141.63 1058.4 371.85 312.21 29.28 18.0 3.75 8.95 410.0 908.04 108.95 319.15 67.68 155.65 1185.16 351.3 20.4 231.2 521.38 1077.6 317.83 311.2 107.95 439.46 373.74 762.1 367.1 332.16 273.75 164.03 424.03 460.55 137.4 378.96 435.88 694.2 1523.2 621.22 260.64 345.27 303.62 106.25 843.01 726.57 194.53 231.9 307.65 326.13 137.95 867.89 236.69 672.0 149.1 990.0 298.99 630.39 334.65 130.8 18.0 6.7 216.6 109.4 32.25 24.15 11.8 532.28 538.11 117.13 59.5 126.8 48.05 220.9 138.24 103.95 351.6 227.25 79.6 159.1 230.2 452.95 233.71 434.15 502.54 136.75 350.55 796.55 15.0 224.1 478.74 97.11 760.69 148.3 130.32 549.77 450.84 146.62 689.5 256.2 304.1 203.32 281.02 870.28 283.15 269.15 309.1 567.71 441.63 689.9 139.25 316.74 188.69 260.65 413.44 253.55 817.44 950.69 720.79 305.5 118.26 933.35 183.6 280.94 204.24 242.96 212.13 619.24 204.65 748.42 211.62 533.14 302.5 1450.2 21.25 289.3 132.4 186.6 125.94 90.0 81.3 647.82 266.19 547.73 175.2 12.75 192.27 671.56 406.7 355.13 285.64 101.4 582.12 391.92 98.16 25.46 450.84 626.6 235.13 137.75 147.4 504.54 21.95 474.32 213.65 235.84 150.4 10.97 436.18 255.0 533.97 182.01 118.25 48.89 161.8 166.95 378.05 263.68 560.58 221.9 209.41 504.54 346.0 294.8 716.35 34.0 311.2 504.54 463.0 41.3 808.12 367.9 14.3 411.2 187.19 287.49 682.4 191.74 426.0 173.55 163.77 218.33 211.62 312.65 610.95 224.98 214.8 44.7 362.6 425.09 452.16 147.1 321.0 51.0 446.4 990.48 208.83 380.84 76.5 238.85 312.33 214.17 143.7 488.16 660.96 156.5 242.1 696.54 451.44 151.72 380.65 379.16 293.35 164.75 285.9 413.0 74

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
total_amount = amount_df_85.select("total_amount")

show_distribution(total_amount)

Minimum:0.19
Mean:266.91
Median:252.96
Mode:15.00
Maximum:692.84



total_amount 505.3 145.8 630.33 310.75 426.3 50.4 344.34 382.37 285.06 141.0 308.44 130.0 570.24 196.1 485.79 589.33 148.3 251.1 255.5 282.46 1.4 229.46 145.0 304.53 192.75 367.41 633.33 537.96 387.6 281.82 124.95 584.5 641.45 390.86 482.3 278.61 379.65 603.94 291.58 128.6 246.86 229.6 322.9 218.55 307.8 282.28 156.71 507.49 580.02 551.33 367.28 319.66 219.82 261.0 124.83 293.95 21.95 105.85 263.42 362.78 423.87 322.33 17.0 420.29 337.2 440.07 311.55 383.87 2.1 446.98 9.75 553.78 2.95 629.78 12.75 408.85 499.36 409.27 198.0 6.35 19.5 17.4 352.85 535.9 7.5 31.2 329.91 622.1 12.85 261.74 173.1 294.14 60.78 222.12 55.2 23.48 73.75 374.43 252.3 263.09 538.46 378.12 397.2 114.6 61.1 261.3 192.0 189.3 45.0 89.59 125.73 266.6 221.53 299.7 306.95 401.7 17.0 216.0 180.45 168.0 538.77 223.1 285.59 130.18 159.98 230.46 162.04 40.8 333.67 216.86 319.54 119.16 80.4 131.12 221.19 260.36 58.2 311.5 200.63 311.69 408.07 128.48 174.52 251.17 454.35 180.13 109.84 112.5 493.25 634.29 597.69 132.55 284.55 340.2 294.3 618.43 371.27 87.3 176.88 174.1 85.95 445.7 472.47 637.04 316.22 150.68 214.8 514.97 89.7 157.91 46.07 66.82 206.85 234.87 118.95 675.0 39.98 162.1 632.9 10.2 176.6 530.76 39.85 368.1 143.11 163.47 380.28 578.28 3.61 597.4 181.08 39.8 300.1 520.2 371.82 337.93 260.44 287.37 119.1 203.78 478.7 120.0 202.06 107.33 642.2 144.0 69.6 54.6 336.0 82.6 181.65 430.9 320.4 321.65 154.2 143.06 169.5 114.55 317.55 556.75 344.4 503.93 285.09 221.69 500.55 393.65 308.6 37.8 10.2 45.6 189.15 215.0 58.2 69.82 180.39 228.3 263.85 102.0 13.5 119.54 277.5 61.12 360.52 47.85 314.22 165.3 210.39 355.59 372.2 284.3 161.4 236.25 294.85 194.65 258.1 381.0 115.51 584.35 160.35 311.7 337.9 170.06 17.0 466.2 45.55 636.0 510.87 186.36 279.42 338.5 314.37 110.7 239.68 415.0 30.15 321.21 313.19 39.2 257.62 342.6 122.4 317.04 108.75 112.03 319.87 297.05 569.18 241.8 197.3 151.65 387.87 174.85 160.69 339.78 210.55 407.22 308.75 337.1 510.64 160.39 682.65 290.48 455.36 138.0 508.26 19.5 244.8 280.2 141.63 371.85 312.21 29.28 18.0 3.75 8.95 410.0 108.95 319.15 67.68 155.65 351.3 20.4 231.2 521.38 317.83 311.2 107.95 439.46 373.74 367.1 332.16 273.75 164.03 424.03 460.55 137.4 378.96 435.88 621.22 260.64 345.27 303.62 106.25 194.53 231.9 307.65 326.13 137.95 236.69 672.0 149.1 298.99 630.39 334.65 130.8 18.0 6.7 216.6 109.4 32.25 24.15 11.8 532.28 538.11 117.13 59.5 126.8 48.05 220.9 138.24 103.95 351.6 227.25 79.6 159.1 230.2 452.95 233.71 434.15 502.54 136.75 350.55 15.0 224.1 478.74 97.11 148.3 130.32 549.77 450.84 146.62 689.5 256.2 304.1 203.32 281.02 283.15 269.15 309.1 567.71 441.63 689.9 139.25 316.74 188.69 260.65 413.44 253.55 305.5 118.26 183.6 280.94 204.24 242.96 212.13 619.24 204.65 211.62 533.14 302.5 21.25 289.3 132.4 186.6 125.94 90.0 81.3 647.82 266.19 547.73 175.2 12.75 192.27 671.56 406.7 355.13 285.64 101.4 582.12 391.92 98.16 25.46 450.84 626.6 235.13 137.75 147.4 504.54 21.95 474.32 213.65 235.84 150.4 10.97 436.18 255.0 533.97 182.01 118.25 48.89 161.8 166.95 378.05 263.68 560.58 221.9 209.41 504.54 346.0 294.8 34.0 311.2 504.54 463.0 41.3 367.9 14.3 411.2 187.19 287.49 682.4 191.74 426.0 173.55 163.77 218.33 211.62 312.65 610.95 224.98 214.8 44.7 362.6 425.09 452.16 147.1 321.0 51.0 446.4 208.83 380.84 76.5 238.85 312.33 214.17 143.7 488.16 660.96 156.5 242.1 451.44 151.72 380.65 379.16 293.35 164.75 285.9 413.0 74.56 153.28 307.91 207.9 306.0 195.78 190.47 108.4 378.84 4.25 20.58 154.2 355.38 204.0 45.9 241.05 198.98 332.7 448.96 331.4 4.95 449.95 485.31 668.1 357.87 386.39 7.95 343.44 561.6 285.35 221.52 412.6 306.55 389.62 25.5 8.92 580.64 312.96 356.4 322.65 302.78 338.34 425.59 182.88 10.0 255.04 323.39 306.45 44.32 221.0 135.94 30.6 192.55 155.7 28.75 7.8 660.0 19.5 207.32 487.09 215.0 39.4 134.04 159.0 259.92 309.7 304.8 564.38 2.9 20.25 129.3 249.64 311.8 363.6 88.05 211.41 10.0 111.24 656.85 312.9 109.08 42.3 114.3 123.1 648.5 250.02 304.2 404.44 81.12 12.4 366.9 215.3 0.95 644.52 151.2 97.55 15.0 6.35 11.8 0.85 102.82 8.7 328.8 507.9

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

# Monthly Placed and Canceled Orders

In [0]:
from pyspark.sql.functions import col, countDistinct, date_format

cancelation_df = retail_df.withColumn("is_canceled", col("invoice_no").startswith('C'))
cancelation_df = cancelation_df.withColumn("ym", date_format(col("invoice_date"), "yyyyMM"))
# Calculate amount
amount_df = retail_df.withColumn("amount", col("quantity") * col("unit_price"))
amount_df = amount_df.withColumn("ym", date_format(col("invoice_date"), "yyyyMM"))

# Filter out placed invoices and count distinct invoice_no
monthly_placed_df = cancelation_df.filter(col("is_canceled") == False)
monthly_placed_df = monthly_placed_df.groupBy("ym").agg(countDistinct("invoice_no").alias("monthly_placed"))

# Filter out canceled invoices and count distinct invoice_no
cancelation_df = cancelation_df.filter(col("is_canceled") == True)
cancelation_df = cancelation_df.groupBy("ym").agg(countDistinct("invoice_no").alias("monthly_canceled"))

# Concatenate (join) the two DataFrames on the "ym" column
final_df = monthly_placed_df.join(cancelation_df, "ym", "outer")

#final_df.show()
display(final_df)


ym monthly_placed monthly_canceled 200912 1929 401 201001 1333 300 201002 1729 240 201003 1960 407 201004 1588 304 201005 2011 407 201006 1859 357 201007 1673 344 201008 1604 273 201009 2004 371 201010 2489 476 201011 3093 576 201012 1699 326 201101 1216 260 201102 1174 219 201103 1665 318 201104 1504 240 201105 1848 314 201106 1683 329 201107 1657 270 201108 1459 278 201109 1994 333 201110 2275 362 201111 3021 441 201112 869 146

Databricks visualization. Run in Databricks to view.

# Monthly Sales

In [0]:
from pyspark.sql.functions import sum

# Calculate amount
amount_df = retail_df.withColumn("amount", col("quantity") * col("unit_price"))
amount_df = amount_df.withColumn("ym", date_format(col("invoice_date"), "yyyyMM"))

amount_df = amount_df.groupBy("ym").agg(
    round(sum("amount"), 2).alias("Sales(Million)")
)

display(amount_df)

ym Sales(Million) 201001 624032.89 201002 533091.43 200912 799847.11 201003 765848.76 201007 575236.36 201004 590580.43 201006 679786.61 201005 615322.83 201103 683267.08 201010 1045168.35 201009 853650.43 201008 656776.34 201012 1126445.47 201011 1422654.64 201104 493207.12 201106 691123.12 201102 498062.65 201105 723333.51 201108 682680.51 201101 560000.26 201110 1070704.67 201107 681300.11 201109 1019687.62 201111 1461756.25 201112 433686.01

Databricks visualization. Run in Databricks to view.

# Monthly Sales Growth


In [0]:
from pyspark.sql.functions import lag
from pyspark.sql.window import Window

# Define a window specification to calculate previous row
window_spec = Window.orderBy("ym")

# Add the previous row's 'Sales(Million)' using lag function
amount_df = amount_df.withColumn("previous_amount", lag("Sales(Million)").over(window_spec))

# Calculate the percentage growth
amount_df = amount_df.withColumn("pct_growth", 
                                 (col("Sales(Million)") - col("previous_amount")) / col("previous_amount") * 100)

display(amount_df)

ym Sales(Million) previous_amount pct_growth 200912 799847.11 null null 201001 624032.89 799847.11 -21.98097833972295 201002 533091.43 624032.89 -14.57318379484773 201003 765848.76 533091.43 43.66180300441144 201004 590580.43 765848.76 -22.885501570832332 201005 615322.83 590580.43 4.189505568276264 201006 679786.61 615322.83 10.47641609527149 201007 575236.36 679786.61 -15.379863101451793 201008 656776.34 575236.36 14.175039282982734 201009 853650.43 656776.34 29.975819469988842 201010 1045168.35 853650.43 22.435169393635743 201011 1422654.64 1045168.35 36.117271442442735 201012 1126445.47 1422654.64 -20.82087680816195 201101 560000.26 1126445.47 -50.28607465570437 201102 498062.65 560000.26 -11.060282364868899 201103 683267.08 498062.65 37.184966590046436 201104 493207.12 683267.08 -27.81634964763705 201105 723333.51 493207.12 46.659178399533246 201106 691123.12 723333.51 -4.453048221144906 201107 681300.11 691123.12 -1.421311155094914 201108 682680.51 681300.11 0.20261261956937351 201109 1019687.62 682680.51 49.36527483405085 201110 1070704.67 1019687.62 5.003203824324152 201111 1461756.25 1070704.67 36.52282379603333 201112 433686.01 1461756.25 -70.33116773059804

Databricks visualization. Run in Databricks to view.

# Monthly Active Users

In [0]:
user_df = retail_df.withColumn("ym", date_format(col("invoice_date"), "yyyyMM"))
user_df = user_df.groupBy("ym").agg(countDistinct("customer_id"))
display(user_df)

ym count(customer_id) 201103 1020 201001 786 201002 807 201010 1577 201009 1202 201104 899 201106 1051 201102 798 201110 1425 201008 964 201107 993 201012 948 201105 1079 201109 1302 201011 1683 201007 988 201111 1711 201108 980 201112 686 201004 998 200912 1045 201006 1095 201005 1062 201101 783 201003 1111

Databricks visualization. Run in Databricks to view.

# New and Existing Users



In [0]:
from pyspark.sql.functions import col, min, date_format, countDistinct

# Add 'ym' to the main retail_df first
retail_df = retail_df.withColumn("ym", date_format(col("invoice_date"), "yyyyMM"))

# Then create the first purchase DataFrame
first_purchase_df = retail_df.groupBy("customer_id").agg(
    min("ym").alias("first_purchase_ym")
)

# Join the first purchase info back to the full dataset (retail_df already has 'ym')
retail_df_with_first_purchase = retail_df.join(
    first_purchase_df, on="customer_id", how="left"
)

# Identify new users: ym == first_purchase_ym
new_user_df = retail_df_with_first_purchase.filter(col("ym") == col("first_purchase_ym"))
new_user_count = new_user_df.groupBy("ym").agg(countDistinct("customer_id").alias("new_user_count"))

# Identify existing users: ym > first_purchase_ym
ex_user_df = retail_df_with_first_purchase.filter(col("ym") > col("first_purchase_ym"))
ex_user_count = ex_user_df.groupBy("ym").agg(countDistinct("customer_id").alias("ex_user_count"))

# Merge new and existing user counts
user_count_df = new_user_count.join(ex_user_count, on="ym", how="outer").fillna(0)

display(user_count_df)


ym new_user_count ex_user_count 200912 1045 0 201001 394 392 201002 363 444 201003 436 675 201004 291 707 201005 254 808 201006 269 826 201007 183 805 201008 158 806 201009 242 960 201010 379 1198 201011 322 1361 201012 77 871 201101 71 712 201102 123 675 201103 178 842 201104 105 794 201105 108 971 201106 108 943 201107 102 891 201108 106 874 201109 187 1115 201110 221 1204 201111 192 1519 201112 28 658

Databricks visualization. Run in Databricks to view.

## Finding RFM

RFM is a method used for analyzing customer value. It is commonly used in database marketing and direct marketing and has received particular attention in the retail and professional services industries. ([wikipedia](https://en.wikipedia.org/wiki/RFM_(market_research)))


RFM stands for three dimensions:

- Recency – How recently did the customer purchase?

- Frequency – How often do they purchase?

- Monetary Value – How much do they spend?


In [0]:
from pyspark.sql.functions import max, datediff, lit, to_date, count

amount_df = retail_df.withColumn("amount", col("quantity") * col("unit_price"))

current_date = to_date(lit("2025-02-05"))

# Get last purchase date per customer
recency_df = amount_df.groupBy("customer_id").agg(
    max("invoice_date").alias("last_purchase_date")
)

# Calculate Recency
recency_df = recency_df.withColumn(
    "recency", datediff(current_date, col("last_purchase_date"))
)
recency_df = recency_df.select("customer_id", "recency")

# Calculate Frequency
frequency_df = retail_df.groupBy("customer_id").agg(
    countDistinct("invoice_no").alias("frequency")
)

# Calculate Monetary 
monetary_df = amount_df.groupBy("customer_id").agg(round(
    sum("amount"),2).alias("monetary"))

rfm_df = recency_df.join(frequency_df, on="customer_id", how="inner")
rfm_df = rfm_df.join(monetary_df, on="customer_id", how="inner")

display(rfm_df)


customer_id recency frequency monetary 18051 5441 8 2275.98 13623 4837 15 2446.36 14832 5437 3 -274.63 17389 4807 77 54587.03 15447 5137 6 484.93 15727 4823 15 9445.51 17753 5271 5 388.06 17679 4859 11 3166.56 13285 4830 6 3364.59 13289 5530 1 307.95 16574 4878 3 1301.78 16861 4866 6 902.37 16503 4913 13 3597.89 14450 4987 7 1128.44 12799 5336 1 219.35 15957 4838 3 930.1 13832 4824 3 602.44 13840 5223 1 651.4 14570 5087 3 613.75 15846 5192 1 107.01 17420 4857 8 1074.53 16386 4835 3 1102.59 16339 5091 1 109.95 18024 4959 3 236.78 12940 4853 4 876.29 15619 4817 1 336.4 15790 4817 1 220.85 12471 4809 129 37948.61 15100 5137 14 2319.5 15538 5344 11 3027.15 18201 5529 1 447.53 14465 5053 11 3946.03 15967 4830 13 3019.2 15003 5280 7 1055.7 14514 4868 10 4594.73 13622 5495 2 651.45 15254 4934 4 1073.4 14423 5025 4 914.96 18218 5013 6 1106.3 17172 4881 6 910.99 14075 4811 6 1734.87 16500 4811 10 835.96 14876 5328 2 256.7 14148 5040 2 466.29 16916 4830 4 1123.4 17688 5181 2 286.5 17607 5183 1 333.81 18161 4817 7 1797.2 14536 5066 1 171.8 13261 5075 2 944.1 12626 4830 13 6388.35 18282 4814 3 176.6 15004 4954 1 1246.32 12715 4913 1 353.86 12611 4859 1 1193.32 12367 4811 1 168.9 15738 4825 45 13342.12 16283 4812 12 4311.37 17044 4815 16 11867.6 15296 4851 20 10223.93 16791 4836 18 3946.12 17809 4823 24 10498.85 15162 5535 2 241.5 17754 4807 16 4509.39 13875 4860 14 4814.37 13648 5207 11 1679.01 17028 5388 3 1593.83 14714 4831 7 896.4 13009 5479 1 234.0 16534 5449 1 635.9 14420 4892 7 1627.72 14997 4853 5 771.38 14324 5216 2 701.61 14837 4896 12 3445.82 12998 5299 4 897.38 17077 5385 1 306.0 13207 4822 4 535.86 16680 4850 3 821.45 17783 4879 3 379.91 15173 5187 8 1399.26 15207 5216 5 653.77 13601 4852 4 1185.14 13910 5250 1 -127.66 17008 5236 1 81.36 17708 4994 4 887.93 12393 4879 7 2376.75 17751 5228 1 157.86 18221 4829 8 1370.34 14377 4998 2 617.05 15655 5040 2 511.32 13060 5060 1 307.53 17775 5061 1 56.4 14289 4815 6 911.26 17837 4849 10 1560.53 16924 4828 4 739.5 13483 4872 1 140.34 13508 5050 2 287.05 13916 5270 5 1260.51 15382 4821 20 13646.5 17193 4842 12 2254.6 14315 4828 10 3168.72 14958 4954 6 957.94 12366 5440 1 500.24 15575 5426 1 30.1 17437 5336 1 373.17 14809 5428 2 686.76 13465 5253 2 931.12 13898 5132 2 686.4 16224 4864 5 1616.54 17223 5117 3 873.53 18043 4831 3 875.97 16828 4900 2 128.5 15604 4859 1 216.39 17712 4851 1 522.91 13188 4818 1 114.6 14944 4836 24 9674.92 17190 4865 8 1548.04 17113 5312 8 2109.16 13795 5195 4 836.3 13225 4810 17 15879.27 14713 4816 25 5372.47 13329 4838 14 4977.02 17950 4879 8 1412.65 16094 4818 19 3599.16 13765 5460 1 352.82 14770 5039 9 3624.89 16232 4839 10 2692.02 16117 4996 4 650.05 16565 5171 5 700.45 15960 5181 5 394.0 15535 4980 10 985.82 13398 4999 2 670.34 14779 5087 3 386.15 15292 5008 1 180.94 16706 4844 3 531.35 16999 4830 2 484.82 15740 4856 1 154.88 12607 4865 2 0.0 15429 4833 3 364.9 13923 4860 1 351.13 13504 4871 1 295.93 14660 4893 2 285.74 17836 4854 1 110.21 17154 4882 1 329.34 14752 4850 1 389.64 16985 4824 26 10545.76 17438 5054 6 1412.62 13468 4808 87 13091.61 14365 5201 2 634.68 16027 4898 18 1799.84 15221 5173 7 1816.1 16549 4817 37 13159.64 16119 4815 8 1720.81 16510 5179 6 2100.0 15070 5179 3 843.25 13997 5326 3 382.31 17346 4810 27 5258.02 14874 5342 1 116.18 16526 4978 2 717.21 14846 5230 2 406.8 12694 4877 4 1839.45 15647 5222 1 169.0 15462 4901 4 737.05 15026 4887 5 1061.61 13500 4830 5 1436.3 17036 5190 1 176.9 14458 5187 1 237.42 15146 4971 3 1313.66 15594 4822 6 1767.53 16506 4826 2 90.3 14124 4891 1 419.58 16295 4816 4 1328.55 14054 4872 1 92.46 17677 4808 91 35866.63 15827 4880 42 3430.96 13313 4829 15 3423.27 15983 4829 8 3958.82 17213 4847 20 5078.93 14030 4825 22 8145.59 16255 4823 19 4834.39 14477 4826 10 1960.61 15584 4830 7 1275.0 12530 4866 12 3689.86 13544 4846 7 820.5 14284 4837 4 1282.85 15558 5446 2 143.33 16391 5207 4 1103.61 16601 4847 3 684.25 12717 4958 4 1258.91 15216 4894 2 486.09 14812 5405 1 185.8 15931 5235 1 239.9 17782 5189 2 679.02 17378

# RFM Segmentation

In [0]:
from pyspark.sql.functions import ntile, concat_ws

recency_window = Window.orderBy(col("recency").asc())
frequency_window = Window.orderBy(col("frequency").desc())
monetary_window = Window.orderBy(col("monetary").desc())

rfm_df = rfm_df.withColumn("recency_score", ntile(5).over(recency_window))
rfm_df = rfm_df.withColumn("frequency_score", ntile(5).over(frequency_window))
rfm_df = rfm_df.withColumn("monetary_score", ntile(5).over(monetary_window))

# Concatenate scores to get RFM score
rfm_df = rfm_df.withColumn(
    "rfm_score",
    concat_ws("", col("recency_score").cast("string"),
                  col("frequency_score").cast("string"),
                  col("monetary_score").cast("string"))
)

display(rfm_df)

customer_id recency frequency monetary recency_score frequency_score monetary_score rfm_score 18102 4807 153 598215.22 1 1 1 111 14646 4808 164 523342.07 1 1 1 111 14156 4816 202 296564.69 1 1 1 111 14911 4808 510 270248.53 1 1 1 111 17450 4815 61 233579.39 1 1 1 111 13694 4810 164 190825.52 1 1 1 111 17511 4809 85 171885.98 1 1 1 111 12415 4831 33 143269.29 2 1 1 211 16684 4811 65 141502.25 1 1 1 111 15061 4810 138 136391.48 1 1 1 111 15311 4807 270 113513.07 1 1 1 111 13089 4809 247 113214.19 1 1 1 111 17949 4808 138 98895.59 1 1 1 111 16029 4845 125 91800.91 2 1 1 211 14298 4810 84 90489.31 1 1 1 111 15769 4814 51 84269.38 1 1 1 111 13798 4808 125 73573.47 1 1 1 111 15838 4818 38 73404.11 1 1 1 111 12931 4828 71 71299.67 2 1 1 211 17841 4808 289 69516.19 1 1 1 111 14088 4817 20 62400.02 1 1 1 111 16422 4824 146 61110.54 1 1 1 111 13081 4808 44 58328.15 1 1 1 111 14096 4811 34 57120.91 1 1 1 111 16754 5179 35 56560.58 4 1 1 411 13777 4807 73 56016.57 1 1 1 111 17850 5109 159 55703.13 4 1 1 411 14680 4832 87 54801.34 2 1 1 211 17389 4807 77 54587.03 1 1 1 111 13093 5074 88 54073.73 4 1 1 411 16013 4810 94 52788.92 1 1 1 111 13408 4808 135 50852.85 1 1 1 111 12748 4807 365 49970.13 1 1 1 111 17404 4811 28 46006.82 1 1 1 111 13881 4810 51 44392.5 1 1 1 111 16705 4807 61 42653.14 1 1 1 111 17381 4815 39 39999.19 1 1 1 111 15039 4816 107 39742.99 1 1 1 111 16210 4808 37 38304.06 1 1 1 111 14031 4814 55 38025.97 1 1 1 111 12471 4809 129 37948.61 1 1 1 111 17675 4808 90 37605.84 1 1 1 111 17677 4808 91 35866.63 1 1 1 111 13767 4809 96 35115.68 1 1 1 111 12921 4810 103 34639.45 1 1 1 111 12678 4849 23 33851.13 2 1 1 211 15856 4811 58 33817.44 1 1 1 111 16779 4809 62 32981.61 1 1 1 111 17428 4807 51 31238.06 1 1 1 111 14258 4816 32 31027.35 1 1 1 111 12681 4821 56 30551.76 1 1 1 111 13902 5439 8 30411.26 5 2 1 521 12709 4810 55 30312.61 1 1 1 111 14606 4808 259 30094.38 1 1 1 111 13078 4808 95 28883.83 1 1 1 111 13098 4808 41 28658.88 1 1 1 111 17857 4810 26 28566.54 1 1 1 111 15513 4838 41 27264.45 2 1 1 211 17940 4856 22 26960.02 2 1 1 211 16333 4814 22 26626.8 1 1 1 111 18251 4894 9 26278.86 3 2 1 321 14527 4809 190 25774.54 1 1 1 111 12731 4830 19 25673.21 2 1 1 211 17865 4837 62 25649.05 2 1 1 211 13802 4945 24 25491.56 3 1 1 311 14062 4816 27 25434.83 1 1 1 111 12939 4871 20 25264.8 3 1 1 311 12621 4808 44 24579.31 1 1 1 111 17920 4811 56 24509.91 1 1 1 111 14895 4814 48 24488.82 1 1 1 111 13001 4811 37 24136.05 1 1 1 111 12682 4810 53 23945.81 1 1 1 111 15498 4807 55 23860.81 1 1 1 111 15640 4811 34 23835.41 1 1 1 111 16525 4809 54 23350.74 1 1 1 111 12409 4885 13 23090.47 3 1 1 311 16133 4810 78 22228.88 1 1 1 111 12540 4826 36 22107.29 2 1 1 211 14051 4807 42 22104.5 1 1 1 111 13340 4852 12 22100.56 2 1 1 211 15159 4808 38 22049.4 1 1 1 111 12482 5256 32 21893.53 5 1 1 511 14667 4817 61 21720.59 1 1 1 111 13319 4812 78 21706.09 1 1 1 111 15749 5042 4 21535.9 4 3 1 431 17340 4816 30 21411.64 1 1 1 111 15615 4817 54 21282.07 1 1 1 111 12753 4810 11 21024.01 1 1 1 111 16839 4815 51 20968.27 1 1 1 111 17243 4808 80 20709.21 1 1 1 111 14866 4817 20 20657.77 1 1 1 111 12433 4807 11 20428.86 1 1 1 111 12477 4829 12 20173.64 2 1 1 211 15251 4816 31 20095.6 1 1 1 111 18008 4877 23 19787.13 3 1 1 311 17706 4811 43 19543.9 1 1 1 111 16843 4849 38 19528.78 2 1 1 211 17139 4822 29 19491.61 1 1 1 111 14607 4822 27 18745.56 1 1 1 111 12557 4823 8 18716.14 1 2 1 121 14194 4811 54 18442.87 1 1 1 111 12357 4840 3 18287.66 2 3 1 231 15808 5113 24 18248.83 4 1 1 411 17581 4807 53 18247.47 1 1 1 111 16746 4811 46 18031.85 1 1 1 111 17377 4830 91 17851.41 2 1 1 211 12647 4829 45 17682.79 2 1 1 211 15078 4814 64 17576.52 1 1 1 111 16652 4860 24 17312.83 2 1 1 211 18172 4821 63 17301.83 1 1 1 111 14952 4853 43 17244.25 2 1 1 211 17416 4836 25 17221.47 2 1 1 211 15523 4891 18 17220.04 3 1 1 311 17735 4809 29 17162.58 1 1 1 111 13027 4920 23 17148.0 3 1 1 311 15189 4808 58 17101.13 1 1 1 111 12472 4837 37 16956.69 2 1 1 211 15358 4811 55 16837.35 1 1

In [0]:
from pyspark.sql.functions import concat_ws, udf
from pyspark.sql.types import StringType

rfm_df = rfm_df.withColumn(
    "rf_segment", concat_ws("", col("recency_score").cast("string"), col("frequency_score").cast("string"))
)

seg_map = {
    "11": "Hibernating", "12": "Hibernating", "21": "Hibernating", "22": "Hibernating",
    "13": "At Risk", "14": "At Risk", "23": "At Risk", "24": "At Risk",
    "25": "Can't Lose",
    "31": "About to Sleep", "32": "About to Sleep",
    "33": "Need Attention",
    "34": "Loyal Customers", "35": "Loyal Customers",
    "44": "Loyal Customers", "45": "Loyal Customers",
    "41": "Promising",
    "51": "New Customers",
    "42": "Potential Loyalists", "43": "Potential Loyalists",
    "52": "Potential Loyalists", "53": "Potential Loyalists",
    "54": "Champions", "55": "Champions"
}

def segment_lookup(rf_segment):
    return seg_map.get(rf_segment, "Other")

segment_udf = udf(segment_lookup, StringType())

rfm_df = rfm_df.withColumn("segment", segment_udf(col("rf_segment")))

display(rfm_df)

customer_id recency frequency monetary recency_score frequency_score monetary_score rfm_score rf_segment segment 18102 4807 153 598215.22 1 1 1 111 11 Hibernating 14646 4808 164 523342.07 1 1 1 111 11 Hibernating 14156 4816 202 296564.69 1 1 1 111 11 Hibernating 14911 4808 510 270248.53 1 1 1 111 11 Hibernating 17450 4815 61 233579.39 1 1 1 111 11 Hibernating 13694 4810 164 190825.52 1 1 1 111 11 Hibernating 17511 4809 85 171885.98 1 1 1 111 11 Hibernating 12415 4831 33 143269.29 2 1 1 211 21 Hibernating 16684 4811 65 141502.25 1 1 1 111 11 Hibernating 15061 4810 138 136391.48 1 1 1 111 11 Hibernating 15311 4807 270 113513.07 1 1 1 111 11 Hibernating 13089 4809 247 113214.19 1 1 1 111 11 Hibernating 17949 4808 138 98895.59 1 1 1 111 11 Hibernating 16029 4845 125 91800.91 2 1 1 211 21 Hibernating 14298 4810 84 90489.31 1 1 1 111 11 Hibernating 15769 4814 51 84269.38 1 1 1 111 11 Hibernating 13798 4808 125 73573.47 1 1 1 111 11 Hibernating 15838 4818 38 73404.11 1 1 1 111 11 Hibernating 12931 4828 71 71299.67 2 1 1 211 21 Hibernating 17841 4808 289 69516.19 1 1 1 111 11 Hibernating 14088 4817 20 62400.02 1 1 1 111 11 Hibernating 16422 4824 146 61110.54 1 1 1 111 11 Hibernating 13081 4808 44 58328.15 1 1 1 111 11 Hibernating 14096 4811 34 57120.91 1 1 1 111 11 Hibernating 16754 5179 35 56560.58 4 1 1 411 41 Promising 13777 4807 73 56016.57 1 1 1 111 11 Hibernating 17850 5109 159 55703.13 4 1 1 411 41 Promising 14680 4832 87 54801.34 2 1 1 211 21 Hibernating 17389 4807 77 54587.03 1 1 1 111 11 Hibernating 13093 5074 88 54073.73 4 1 1 411 41 Promising 16013 4810 94 52788.92 1 1 1 111 11 Hibernating 13408 4808 135 50852.85 1 1 1 111 11 Hibernating 12748 4807 365 49970.13 1 1 1 111 11 Hibernating 17404 4811 28 46006.82 1 1 1 111 11 Hibernating 13881 4810 51 44392.5 1 1 1 111 11 Hibernating 16705 4807 61 42653.14 1 1 1 111 11 Hibernating 17381 4815 39 39999.19 1 1 1 111 11 Hibernating 15039 4816 107 39742.99 1 1 1 111 11 Hibernating 16210 4808 37 38304.06 1 1 1 111 11 Hibernating 14031 4814 55 38025.97 1 1 1 111 11 Hibernating 12471 4809 129 37948.61 1 1 1 111 11 Hibernating 17675 4808 90 37605.84 1 1 1 111 11 Hibernating 17677 4808 91 35866.63 1 1 1 111 11 Hibernating 13767 4809 96 35115.68 1 1 1 111 11 Hibernating 12921 4810 103 34639.45 1 1 1 111 11 Hibernating 12678 4849 23 33851.13 2 1 1 211 21 Hibernating 15856 4811 58 33817.44 1 1 1 111 11 Hibernating 16779 4809 62 32981.61 1 1 1 111 11 Hibernating 17428 4807 51 31238.06 1 1 1 111 11 Hibernating 14258 4816 32 31027.35 1 1 1 111 11 Hibernating 12681 4821 56 30551.76 1 1 1 111 11 Hibernating 13902 5439 8 30411.26 5 2 1 521 52 Potential Loyalists 12709 4810 55 30312.61 1 1 1 111 11 Hibernating 14606 4808 259 30094.38 1 1 1 111 11 Hibernating 13078 4808 95 28883.83 1 1 1 111 11 Hibernating 13098 4808 41 28658.88 1 1 1 111 11 Hibernating 17857 4810 26 28566.54 1 1 1 111 11 Hibernating 15513 4838 41 27264.45 2 1 1 211 21 Hibernating 17940 4856 22 26960.02 2 1 1 211 21 Hibernating 16333 4814 22 26626.8 1 1 1 111 11 Hibernating 18251 4894 9 26278.86 3 2 1 321 32 About to Sleep 14527 4809 190 25774.54 1 1 1 111 11 Hibernating 12731 4830 19 25673.21 2 1 1 211 21 Hibernating 17865 4837 62 25649.05 2 1 1 211 21 Hibernating 13802 4945 24 25491.56 3 1 1 311 31 About to Sleep 14062 4816 27 25434.83 1 1 1 111 11 Hibernating 12939 4871 20 25264.8 3 1 1 311 31 About to Sleep 12621 4808 44 24579.31 1 1 1 111 11 Hibernating 17920 4811 56 24509.91 1 1 1 111 11 Hibernating 14895 4814 48 24488.82 1 1 1 111 11 Hibernating 13001 4811 37 24136.05 1 1 1 111 11 Hibernating 12682 4810 53 23945.81 1 1 1 111 11 Hibernating 15498 4807 55 23860.81 1 1 1 111 11 Hibernating 15640 4811 34 23835.41 1 1 1 111 11 Hibernating 16525 4809 54 23350.74 1 1 1 111 11 Hibernating 12409 4885 13 23090.47 3 1 1 311 31 About to Sleep 16133 4810 78 22228.88 1 1 1 111 11 Hibernating 12540 4826 36 22107.29 2 1 1 211 21 Hibernating 14051 4807 42 22104.5 1 1 1 111 11 Hibernating 13340 4852 12 22100.56 2 1 1 211 21 Hibernating 15159 

In [0]:
from pyspark.sql.functions import avg

agg_df = rfm_df.groupBy("segment").agg(
    round(avg("recency")).alias("avg_recency"),
    round(avg("frequency")).alias("avg_frequency"),
    round(avg("monetary"),2).alias("avg_monetary"),
    count("segment").alias("count")
)

display(agg_df)

segment avg_recency avg_frequency avg_monetary count Champions 5374.0 1.0 287.52 939 Promising 5100.0 19.0 6944.67 58 At Risk 4832.0 2.0 726.91 844 About to Sleep 4912.0 10.0 3175.23 551 Hibernating 4826.0 19.0 7787.51 1534 Potential Loyalists 5168.0 5.0 1233.72 747 Loyal Customers 5049.0 1.0 430.4 997 Need Attention 4921.0 4.0 1026.08 261 New Customers 5277.0 21.0 4355.25 11